<center>
<h1><b>National Health Facilities Datasets Processing</b></h1>
</center>

-----

### Applicant: Banji Raphael Owabumoye

### Importation of Libraries and Loading of Datasets

In [1]:
# importation of libraries
import numpy as np 
import pandas as pd  
import sqlite3  
import geopandas as gpd 
from shapely.geometry import shape 
from shapely import wkt
from shapely.wkt import dumps
import sqlalchemy
from sqlalchemy import create_engine
from shapely.geometry import Polygon

In [2]:
sen_districts = gpd.read_file('lg_senatorial_district.csv', encoding='ISO-8859-1')  # loading of LGA senatorial disticts dataset

hf_locations = gpd.read_file('hf_locations.csv', encoding='ISO-8859-1')  # loading of health facilities locations dataset

admn_bndry = gpd.read_file('C:/Users/Banji/Downloads/datasets/datasets/admin_bndry.shp')  # loading of administrative boundary dataset

personnel_score = gpd.read_file('C:/Users/Banji/Downloads/datasets/datasets/hf_personnel_scoring.tab')  # loading personel score dataset

### Data Assessment and Cleaning

> **Assessment and cleaning of LGA Senatorial District dataset**

In [3]:
sen_districts.head(5)  # display the first five rows of the dataset

s/n    senatorial_district      state       code  \
0   1            Abia North        Abia  SD/001/AB   
1   2          Abia Central        Abia  SD/002/AB   
2   3            Abia South        Abia  SD/003/AB   
3   7   Akwa Ibom North East  Akwa Ibom  SD/007/AK   
4   8  Akwa Ibom North West   Akwa Ibom  SD/008/AK   

                                         composition  \
0    Umunneochi, Isukwuato, Ohafia, Arochukwu, Bende   
1  Umuahia North, Umuahia South, Ikwuano, Isiala ...   
2  Aba North, Aba South, Ugwunagbo, Obingwa,  Ukw...   
3  Etinan, Ibesikpo Asutan, Ibiono Ibom, Itu, Nsi...   
4  Abak, Essien Udim, Etim Ekpo, Ika, Ikono, Ikot...   

                     collation_center  
0        Council Hall Ohafia Lga Hqs   
1  Council Hall Umuahia North Lga Hqs  
2         Aba Town Hall Aba South Lga  
3                 Inec Office Uyo Lga  
4          Inec Office Ikot Ekpenelga

In [4]:
# s/n column will be dropped 
sen_districts= sen_districts.drop(columns =['s/n'])  

In [5]:
sen_districts.head(2) # confirming that s/n column has been dropped

senatorial_district state       code  \
0         Abia North   Abia  SD/001/AB   
1       Abia Central   Abia  SD/002/AB   

                                         composition  \
0    Umunneochi, Isukwuato, Ohafia, Arochukwu, Bende   
1  Umuahia North, Umuahia South, Ikwuano, Isiala ...   

                     collation_center  
0        Council Hall Ohafia Lga Hqs   
1  Council Hall Umuahia North Lga Hqs

In [6]:
# checking if there are any missing values and the correctness of the datatype
sen_districts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109 entries, 0 to 108
Data columns (total 5 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   senatorial_district  109 non-null    object
 1   state                109 non-null    object
 2   code                 109 non-null    object
 3   composition          109 non-null    object
 4   collation_center     109 non-null    object
dtypes: object(5)
memory usage: 4.4+ KB


> **Assessment and cleaning of health facilities locations  dataset**

In [7]:
hf_locations.head(5)  # displaying the first five rows of hf_locations dataset

hf_name     latitude    longitude state_name  \
0     Umuokehi Primary Health Centre     5.585375  7.473098333       Abia   
1       Mkpuka Primary Health Centre  5.283011667  7.326133333       Abia   
2     Etiti Ohazu 4 Igwebuike Ward 7  5.078583333      7.35255       Abia   
3  Okpu Umuobo Primary Health Centre  5.167778333  7.359173333       Abia   
4      Ozuabam Primary Health Centre  5.596001667  7.747691667       Abia   

            lga_name senatorial_district                              globalid  
0      Umuahia North       Abia Central   2d5c9c5e-7626-46f9-b581-dcdc3e4c31e0  
1  Isiala Ngwa South       Abia Central   18b9dcaf-2be5-4d8f-b4d2-2ca8c446ac49  
2          Aba South         Abia South   86f8c4a9-ccbd-405b-8e39-6db4fb7e5603  
3      Osisioma Ngwa         Abia South   6bed7912-7c6a-45ad-8f6a-a98f0f0e1498  
4          Arochukwu         Abia North   6c6e5e73-54c2-467b-a9ad-c9893aa71f5c

In [8]:
# checking if there are any missing values and the correctness of the datatype
hf_locations.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 7 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   hf_name              217 non-null    object
 1   latitude             217 non-null    object
 2   longitude            217 non-null    object
 3   state_name           217 non-null    object
 4   lga_name             217 non-null    object
 5   senatorial_district  217 non-null    object
 6   globalid             217 non-null    object
dtypes: object(7)
memory usage: 12.0+ KB


In [9]:
# changing latitude and longitude columns from object to float datatype
lat_lon = ['latitude', 'longitude']
hf_locations[lat_lon] = hf_locations[lat_lon].astype(float)

In [10]:
hf_locations.info()  # confirming if the datatypes have changed

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 7 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   hf_name              217 non-null    object 
 1   latitude             217 non-null    float64
 2   longitude            217 non-null    float64
 3   state_name           217 non-null    object 
 4   lga_name             217 non-null    object 
 5   senatorial_district  217 non-null    object 
 6   globalid             217 non-null    object 
dtypes: float64(2), object(5)
memory usage: 12.0+ KB


> **Assessment and cleaning of administrative boundary dataset**

In [11]:
# Checking the first five rows of the administrative boundary dataset
admn_bndry.head(5)

lgacode     lganame statename geozone  \
0   29014   Okitipupa      Ondo     SWZ   
1   30006      Boripe      Osun     SWZ   
2   30024      Obokun      Osun     SWZ   
3    4005  Awka North   Anambra     SEZ   
4   16010     Shomgom     Gombe     NEZ   

                                            geometry  
0  POLYGON ((15670.184 2365.362, 15778.128 1446.9...  
1  POLYGON ((5832.368 145677.381, 6210.832 145340...  
2  POLYGON ((3604.194 145424.204, 5201.83 145297....  
3  POLYGON ((254559.646 -12865.891, 254833.164 -1...  
4  POLYGON ((729355.966 350745.403, 729817.183 35...

In [12]:
# checking if there are any missing values and the correctness of the datatype
admn_bndry.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 774 entries, 0 to 773
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype   
---  ------     --------------  -----   
 0   lgacode    774 non-null    object  
 1   lganame    774 non-null    object  
 2   statename  774 non-null    object  
 3   geozone    774 non-null    object  
 4   geometry   774 non-null    geometry
dtypes: geometry(1), object(4)
memory usage: 30.4+ KB


> **Assessment and cleaning of health facilities personnel score  dataset**

In [13]:
# displaying the first five rows of the personnel_score dataset
personnel_score.head(5)

hf_total_score                               hf_uuid
0              5  2d5c9c5e-7626-46f9-b581-dcdc3e4c31e0
1            N/A  18b9dcaf-2be5-4d8f-b4d2-2ca8c446ac49
2             30  86f8c4a9-ccbd-405b-8e39-6db4fb7e5603
3             45  6bed7912-7c6a-45ad-8f6a-a98f0f0e1498
4             40  6c6e5e73-54c2-467b-a9ad-c9893aa71f5c

In [14]:
# to display rows with N/A values
na_rows= personnel_score.query('hf_total_score == "N/A"')
na_rows

hf_total_score                               hf_uuid
1              N/A  18b9dcaf-2be5-4d8f-b4d2-2ca8c446ac49
31             N/A  4d7cbc95-f96f-47c5-a85d-3d1ca2ee6575
34             N/A  ec29f0f3-5ebe-4e02-8a24-7ed3b089cd04
54             N/A  5af4ba28-78e8-4fd1-88c7-1ac3ec5d2489
55             N/A  d347bcc4-36d2-4ead-b844-27b782b57ce3
56             N/A  6e3aa155-2501-4919-8098-6de1c718181f
57             N/A  f8d47d68-165a-464f-ad87-cd2127e46a90
59             N/A  1d11286b-9a1a-40d9-be86-9f3bbcfe162a
70             N/A  8de2848d-ca24-4fb3-9305-cacdb8dd0306
92             N/A  04945de0-cb3c-4ab0-9c5a-7ab0f7723e74
113            N/A  f607faa3-639c-454a-af3a-ef56f3f435f2
117            N/A  bad50675-9c1c-4077-a75b-305e1adf80ab
118            N/A  9e77a440-706a-4d63-9709-b40e8e8e538d
131            N/A  0d29a7de-c09e-4a89-963a-eae88c657a53
154            N/A  f4b33f24-7d2e-452b-b1b2-3d83fb2e690c
155            N/A  09216fd9-000d-4feb-beb7-43da34e4d241
156            N/A  16b10a6b-3d32-465a-8fb7-0f001dc860b8
162            N/A  e989744b-3fd3-4994-98db-9e676e485c00
172            N/A  2f2ff50a-cfbb-4fb4-b385-c65bada3de77
179            N/A  e07c4916-0c90-4902-b5eb-9bd2a6c074b8

In [15]:
# to replace N/A values with nan for the purpose of arithmetic calculation
personnel_score['hf_total_score'] = personnel_score['hf_total_score'].replace('N/A', np.nan)
personnel_score.head(5)

hf_total_score                               hf_uuid
0              5  2d5c9c5e-7626-46f9-b581-dcdc3e4c31e0
1            NaN  18b9dcaf-2be5-4d8f-b4d2-2ca8c446ac49
2             30  86f8c4a9-ccbd-405b-8e39-6db4fb7e5603
3             45  6bed7912-7c6a-45ad-8f6a-a98f0f0e1498
4             40  6c6e5e73-54c2-467b-a9ad-c9893aa71f5c

In [16]:
# changing the hf_total_score column datatype from object to numeric
personnel_score['hf_total_score'] = pd.to_numeric(personnel_score['hf_total_score'])

In [17]:
personnel_score.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   hf_total_score  197 non-null    float64
 1   hf_uuid         217 non-null    object 
dtypes: float64(1), object(1)
memory usage: 3.5+ KB


In [18]:
# Finding the median of values in hf_total_score column
median = personnel_score['hf_total_score'].median()
median

20.0

In [19]:
# Replacing the nan values with the calculated median
personnel_score['hf_total_score'] = personnel_score['hf_total_score'].fillna(median)
personnel_score.head(5)

hf_total_score                               hf_uuid
0             5.0  2d5c9c5e-7626-46f9-b581-dcdc3e4c31e0
1            20.0  18b9dcaf-2be5-4d8f-b4d2-2ca8c446ac49
2            30.0  86f8c4a9-ccbd-405b-8e39-6db4fb7e5603
3            45.0  6bed7912-7c6a-45ad-8f6a-a98f0f0e1498
4            40.0  6c6e5e73-54c2-467b-a9ad-c9893aa71f5c

In [20]:
# checking if there are any missing values and the correctness of the datatype
personnel_score.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   hf_total_score  217 non-null    float64
 1   hf_uuid         217 non-null    object 
dtypes: float64(1), object(1)
memory usage: 3.5+ KB


### SQLite3 Database creation and Loading of Datasets

In [21]:
# Create a new SQLite database
db_path = "C:/Users/Banji/Downloads/datasets/health_facilities.db"

# Connect to SQLite database
engine = create_engine(f"sqlite:///{db_path}")

In [ ]:
"""# Export GeoDataFrames to SQLite
sen_districts.to_sql('sen_districts', con=engine, if_exists='replace', index=False)
hf_locations.to_sql('hf_locations', con=engine, if_exists='replace', index=False)
admn_bndry.to_sql('admn_bndry', con=engine, if_exists='replace', index=False)
personnel_score.to_sql('personnel_score', con=engine, if_exists='replace', index=False)"""

In [ ]:
# Close the SQLAlchemy engine (optional)
engine.dispose()

## Map Visualization

During this project, I attempted to install and configure SpatiaLite to enable spatial capabilities within an SQLite database for use in QGIS. 
Despite multiple attempts and exploring various installation methods, I encountered significant issues with missing modules and compatibility problems.
As a result, I opted for an alternative solution using Jupyter Notebook and the Folium library to create an interactive map.
This approach allowed me to visualize the distribution of health facilities across senatorial districts and highlight the best-ranked facilities.
The interactive map is displayed within this notebook thanks for your understanding


In [23]:
import matplotlib.pyplot as plt
from shapely.geometry import Point
import folium
from folium.plugins import MarkerCluster

In [24]:
# Convert hf_locations to GeoDataFrame
hf_locations['geometry'] = hf_locations.apply(lambda row: Point(row['longitude'], row['latitude']), axis=1)
hf_locations = gpd.GeoDataFrame(hf_locations, geometry='geometry', crs="EPSG:4326")

hf_locations.sample(2)

hf_name  latitude  longitude state_name  \
130  Sumaila Yamma Primary Health Care  11.57072   8.949175       Kano   
33           Jimba Primary Health Care   7.63233   8.337057      Benue   

      lga_name senatorial_district                              globalid  \
130    Sumaila          Kano South  25d9df52-ee2f-4f8d-b180-6a9bdf2aea1f   
33   Gwer-West    Benue North West  47c5a6e2-6443-41c4-885c-bef291065a95   

                     geometry  
130  POINT (8.94918 11.57072)  
33    POINT (8.33706 7.63233)

In [25]:
hf_locations.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 8 columns):
 #   Column               Non-Null Count  Dtype   
---  ------               --------------  -----   
 0   hf_name              217 non-null    object  
 1   latitude             217 non-null    float64 
 2   longitude            217 non-null    float64 
 3   state_name           217 non-null    object  
 4   lga_name             217 non-null    object  
 5   senatorial_district  217 non-null    object  
 6   globalid             217 non-null    object  
 7   geometry             217 non-null    geometry
dtypes: float64(2), geometry(1), object(5)
memory usage: 13.7+ KB


In [28]:
# Merge hf_locations with personnel_score on the unique identifier
hf_locations = hf_locations.merge(personnel_score, left_on='globalid', right_on='hf_uuid', how='left')

In [29]:
# Get the best ranked health facilities in each senatorial district
best_hf = hf_locations.loc[hf_locations.groupby('senatorial_district')['hf_total_score'].idxmax()]

In [30]:
best_hf.columns

Index(['hf_name', 'latitude', 'longitude', 'state_name', 'lga_name',
       'senatorial_district', 'globalid', 'geometry', 'hf_total_score',
       'hf_uuid'],
      dtype='object')

In [34]:
# Merge senatorial districts data
merged_gdf = admn_bndry.merge(sen_districts, left_on='lganame', right_on='composition', how='left')
merged_gdf.columns

Index(['lgacode', 'lganame', 'statename', 'geozone', 'geometry',
       'senatorial_district', 'state', 'code', 'composition',
       'collation_center'],
      dtype='object')

In [35]:
# Create a Folium map centered around Nigeria
m = folium.Map(location=[9.0820, 8.6753], zoom_start=6)

In [36]:
# Add polygons for senatorial districts
for _, row in merged_gdf.iterrows():
    folium.GeoJson(row['geometry'], name=row['senatorial_district']).add_to(m)

In [37]:
# Add health facilities to the map
marker_cluster = MarkerCluster().add_to(m)
for _, row in best_hf.iterrows():
    folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=f"{row['hf_name']} - Score: {row['hf_total_score']}",
        icon=folium.Icon(color='green' if row['hf_total_score'] >= 80 else 'red')
    ).add_to(marker_cluster)

In [38]:
# Add a layer control panel
folium.LayerControl().add_to(m)

# Display the map in the Jupyter Notebook
display(m)

Resources:
https://www.giacomodebidda.com/posts/export-a-geodataframe-to-spatialite/